In [55]:
import time
import numpy as np
import matplotlib.pyplot as plt
from scipy import sparse
from scipy import signal
from prettytable import PrettyTable
from IPython.display import HTML
from matplotlib.animation import FuncAnimation

from IPython.core.display import HTML
HTML("""
<style>
.output_png {
    display: table-cell;
    text-align: center;
    vertical-align: middle;
}
</style>
""")

# Relaxation Method
1) Divide the region of interest into a rectangular grid spanning the region. The region is enclosed by a surface (curve in two dimensions) with specified values of the potential along the curve.

2) Assign to a boundary site the potential of the boundary nearest the site.

3) Assign all interior sites an arbitrary potential (preferably a reasonable guess).

4) Compute new values for the potential V for each interior site. Each new value is obtained by finding the average of the previous values of the potential at the four nearest neighbor sites.

5) Repeat step (4) using the values of V obtained in the previous iteration. This iterative process is continued until the potential at each interior site is computed to the desired accuracy.

# Problem 10.10 Numerical solution of the potential within a rectangular region

In [21]:
# Part (a)
# Part 1 of the relaxation method: create a rectangular grid spanning the region
L = 50
dx = 1
dy = 1
boundary_left = 10
boundary_right = 10
boundary_top = 10
boundary_bottom = 10
threshold = 1e-16

def V(i, j, val):
    return (1/4) * (val[i+1, j] + val[i-1, j] + val[i, j+1] + val[i, j-1])

# Part 3: create our initial guess u_0
u0 = np.zeros([L, L])

# Part 2: assign to a boundary site the potential of the boundary nearest the site
def assign_boundary(u, boundary_left, boundary_right, boundary_top, boundary_bottom):
    temp = np.copy(u)
    temp[:, 0] = boundary_left  # left col
    temp[:, -1] = boundary_right # right col
    temp[0, :] = boundary_top  # top row
    temp[-1, :] = boundary_bottom # bottom row
    return temp
u0 = assign_boundary(u0, boundary_left, boundary_right, boundary_top, boundary_bottom)

# Part 4: compute new values for the potential V for each interior site
def solve_u(u0, do_step, threshold, max_iters=10000):
    start_time = time.time()
    error = 100
    iters = 0
    u_prev = np.zeros(u0.shape)
    u_iter = np.copy(u0)
    while error > threshold and iters < max_iters:
        u_iter = do_step(u_iter)
        error = compute_error(u_iter, u_prev)
        u_prev = np.copy(u_iter)
        iters += 1
    return u_iter, iters, error, (time.time() - start_time)
        
# 5) Repeat step (4) using the values of V obtained in the previous iteration. 
# This iterative process is continued until the potential at each interior site 
# is computed to the desired accuracy.        
def compute_error(u, u_last):
    diffs = np.abs(u - u_last)
    return diffs.mean()

In [22]:
# Define different solving methods using explicit method
def do_step_basic(arr):
    temp = np.copy(arr)
    for i in range(1, L-1):
        for j in range(1, L-1):
            temp[i, j] = V(i, j, arr)
    return temp

def do_step_in_place(u):
    rows, cols = u.shape
    for i in range(1, rows-1):
        for j in range(1, cols-1):
            u[i, j] = V(i, j, u)
    return u

def do_step_gauss_seidel(u):
    rows, cols = u.shape
    # Update black sites
    for i in range(1, L-1):
        if i % 2 == 0:
            for j in range(1, cols-1, 2):
                u[i, j] = V(i, j, u)
        else:
            for j in range(2, cols-1, 2):
                u[i, j] = V(i, j, u)
            
    # Update red sites
    for i in range(1, rows-1):
        if i % 2 == 1:
            for j in range(1, cols-1, 2):
                u[i, j] = V(i, j, u)
        else:
            for j in range(2, cols-1, 2):
                u[i, j] = V(i, j, u)
    return u

def do_step_convolve(u):
    kernel = np.array([[0, 1/4, 0], [1/4, 0, 1/4], [0, 1/4, 0]])
    u_temp = signal.convolve2d(u, kernel, mode='same')
    return assign_boundary(u_temp, boundary_left, boundary_right, boundary_top, boundary_bottom)

w = 1.5
def do_step_overrelax(u):
    kernel1 = np.array([[0, 1/4, 0], [1/4, 0, 1/4], [0, 1/4, 0]])
    kernel2 = np.array([[1/8, 1/8, 1/8], [1/8, 0, 1/8], [1/8, 1/8, 1/8]])
    temp1 = signal.convolve2d(u, kernel1, mode='same')
    temp2 = signal.convolve2d(u, kernel2, mode='same')
    u_temp = w * temp2 + (1-w) * temp1
    return assign_boundary(u_temp, boundary_left, boundary_right, boundary_top, boundary_bottom)

In [23]:
"""
Run all 3 methods and compare number of steps to converge, error, and total time for each
"""
# One step at a time
u_solution, iterations_basic, error_basic, time_basic = solve_u(u0, do_step_basic, threshold)

# Change values in place
u_solution, iterations_inplace, error_inplace, time_inplace = solve_u(u0, do_step_in_place, threshold)

# Compute changes via convolution
u_solution, iterations_convolve, error_convolve, time_convolve = solve_u(u0, do_step_convolve, threshold)

# compute values via the gauss-seidel relaxation
u_solution, iterations_gsr, error_gsr, time_gsr = solve_u(u0, do_step_gauss_seidel, threshold)

# Compute changes via convolution
u_solution, iterations_overrelax, error_overrelax, time_overrelax = solve_u(u0, do_step_overrelax, threshold)

# Plot the results in a table
t = PrettyTable()
t.title = 'Comparison of Explicit FDM Methods'
t.field_names = ['Method', 'Iterations to Convergence', 'Time to Convergence (s)', 'Error']
t.add_row(['One step at a time', iterations_basic, time_basic, error_basic])
t.add_row(['Changes in place', iterations_inplace, time_inplace, error_inplace])
t.add_row(['Convolution', iterations_convolve, time_convolve, error_convolve])
t.add_row(['Gauss-Seidel Relaxation', iterations_gsr, time_gsr, error_gsr])
t.add_row(['Over Relaxation', iterations_overrelax, time_overrelax, error_overrelax])
print(t)

+--------------------------------------------------------------------------------------------------------+
|                                   Comparison of Explicit FDM Methods                                   |
+-------------------------+---------------------------+-------------------------+------------------------+
|          Method         | Iterations to Convergence | Time to Convergence (s) |         Error          |
+-------------------------+---------------------------+-------------------------+------------------------+
|    One step at a time   |           10000           |    20.339675664901733   | 1.5164734179506922e-11 |
|     Changes in place    |            7716           |    15.722506761550903   | 7.176481631177012e-17  |
|       Convolution       |           10000           |    0.8677980899810791   | 1.516472920570777e-11  |
| Gauss-Seidel Relaxation |            7712           |    15.848109006881714   | 9.663381206337362e-17  |
|     Over Relaxation     |          

In [59]:
# Create an animation comparing some of the convergence methods
fig, ax = plt.subplots(1, 3, figsize=(10, 8), dpi=300)
im1 = ax[0].imshow(u0)
im2 = ax[1].imshow(u0)
im3 = ax[2].imshow(u0)

u_basic = np.copy(u0)
u_in_place = np.copy(u0)
u_convolve = np.copy(u0)
def animate(i):
    global u_basic, u_in_place, u_convolve
    if i < 0:
        return
    u_basic = do_step_basic(u_basic)
    u_in_place = do_step_in_place(u_in_place)
    u_convolve = do_step_convolve(u_convolve)
    im1.set_data(u_basic)
    im2.set_data(u_in_place)
    im3.set_data(u_convolve)
    return im1, im2, im3
    
anim = FuncAnimation(fig, animate, interval=50, frames=1000, repeat=False, blit=True)
plt.close(fig)
HTML(anim.to_html5_video())